In [1]:
import boto3
import sagemaker
import io

import pandas as pd
import numpy as np

# load training and validation dataset from Amazon S3
s3_client = boto3.client('s3')
s3_bucket_name='awsml-sagemaker-source'

response = s3_client.get_object(Bucket='awsml-sagemaker-source', Key='boston_train.csv')
response_body = response["Body"].read()
df_boston_train = pd.read_csv(io.BytesIO(response_body), header=0, delimiter=",", low_memory=False)

response = s3_client.get_object(Bucket='awsml-sagemaker-source', Key='boston_test.csv')
response_body = response["Body"].read()
df_boston_test = pd.read_csv(io.BytesIO(response_body), header=0, index_col=False, delimiter=",", low_memory=False)

# extract features and target variable into seperate datasets.
df_boston_train_target = df_boston_train.loc[:,['price']]
df_boston_train_features = df_boston_train.drop(['price'], axis=1)

df_boston_test_target = df_boston_test.loc[:,['price']]
df_boston_test_features = df_boston_test.drop(['price'], axis=1)


In [4]:
# train a linear regression model on a single feature
# the general equation for linear regression is:
# y = w1x1 + w2x2 + ... wnxn + c
#
# in case of a single feature, the equation reduces to:
# y = w1x1 + c

import tensorflow as tf
tf.reset_default_graph()

#
# define a TensorFlow graph
#

# what you will provide:
# x1 =  one-dimensional column array of features
# y_actual = one-dimensional column arrray of expected values/labels
x1 = tf.placeholder(tf.float32, [None, 1], name="x1")
y_actual = tf.placeholder(tf.float32, [None, 1], name="y_actual")

# what you  are interested in:
# w1, c weight and bias term (intercept)
w1 = tf.Variable(tf.zeros([1,1]), name="w1")
c = tf.Variable(tf.zeros([1]), name="c")

# compute y_predicged = w1x1 + c
y_predicted = tf.matmul(x1,w1) + c

# compute cost function
# MSE between predicted and actual values
mse_cost = tf.reduce_mean(tf.square(y_predicted - y_actual))

# create a root node - a gradient descent optimizer, setup to optimise the
# mse_cost function.
learning_rate = 0.00001
train_step = tf.train.GradientDescentOptimizer(learning_rate).minimize(mse_cost)

#
# execute the graph
#
with tf.Session() as sess:
    # use a global_variable_initializer node to initialize
    # variables all variables in the graph (w1 and c)
    init = tf.global_variables_initializer()
    sess.run(init)
    
    # extract CRIM feature and targer variable into arrays
    xin =  df_boston_train_features['CRIM'].values
    yin =  df_boston_train_target['price'].values
    
    xin = np.transpose([xin])
    yin = np.transpose([yin])

    # for each observaiton, evaluate the node called train_step
    # which will in turn update w1 and c so as to minimise
    # the cost function.
    best_w1 = 0.0
    best_c = 0.0
    lowest_cost = 100000.00
    
    num_epochs = 100000
    for i in range(num_epochs):
        input_dict={x1:xin, y_actual:yin}
        sess.run(train_step, feed_dict=input_dict)
        
        computed_w1 = sess.run(w1)
        computed_c = sess.run(c)
        computed_cost = sess.run(mse_cost, feed_dict=input_dict)
        
        if computed_cost < lowest_cost:
            lowest_cost = computed_cost
            best_w1 = computed_w1
            best_c = computed_c
            
        print ("End of epoch %d, w1=%f, c=%f, cost=%f" % (i, computed_w1, computed_c, computed_cost))
    print ("End of training, best_w1=%f, best_c=%f, lowest_cost=%f" % (best_w1, best_c, lowest_cost))
    

End of epoch 0, w1=0.001066, c=0.000448, cost=588.218872
End of epoch 1, w1=0.002129, c=0.000896, cost=588.085815
End of epoch 2, w1=0.003191, c=0.001344, cost=587.953125
End of epoch 3, w1=0.004251, c=0.001791, cost=587.820862
End of epoch 4, w1=0.005309, c=0.002239, cost=587.689026
End of epoch 5, w1=0.006364, c=0.002687, cost=587.557617
End of epoch 6, w1=0.007419, c=0.003134, cost=587.426575
End of epoch 7, w1=0.008471, c=0.003581, cost=587.295959
End of epoch 8, w1=0.009521, c=0.004029, cost=587.165710
End of epoch 9, w1=0.010569, c=0.004476, cost=587.036011
End of epoch 10, w1=0.011616, c=0.004923, cost=586.906616
End of epoch 11, w1=0.012660, c=0.005370, cost=586.777649
End of epoch 12, w1=0.013703, c=0.005817, cost=586.649048
End of epoch 13, w1=0.014744, c=0.006264, cost=586.520874
End of epoch 14, w1=0.015782, c=0.006710, cost=586.393005
End of epoch 15, w1=0.016819, c=0.007157, cost=586.265686
End of epoch 16, w1=0.017854, c=0.007604, cost=586.138733
End of epoch 17, w1=0.01

End of epoch 235, w1=0.204709, c=0.103540, cost=565.797668
End of epoch 236, w1=0.205403, c=0.103970, cost=565.731018
End of epoch 237, w1=0.206095, c=0.104401, cost=565.664551
End of epoch 238, w1=0.206786, c=0.104831, cost=565.598328
End of epoch 239, w1=0.207476, c=0.105261, cost=565.532227
End of epoch 240, w1=0.208165, c=0.105692, cost=565.466431
End of epoch 241, w1=0.208852, c=0.106122, cost=565.400696
End of epoch 242, w1=0.209538, c=0.106552, cost=565.335205
End of epoch 243, w1=0.210223, c=0.106982, cost=565.269775
End of epoch 244, w1=0.210907, c=0.107412, cost=565.204590
End of epoch 245, w1=0.211589, c=0.107842, cost=565.139587
End of epoch 246, w1=0.212270, c=0.108272, cost=565.074768
End of epoch 247, w1=0.212950, c=0.108702, cost=565.010071
End of epoch 248, w1=0.213629, c=0.109132, cost=564.945557
End of epoch 249, w1=0.214306, c=0.109561, cost=564.881287
End of epoch 250, w1=0.214983, c=0.109991, cost=564.817139
End of epoch 251, w1=0.215658, c=0.110421, cost=564.7531

End of epoch 479, w1=0.341300, c=0.206993, cost=553.644470
End of epoch 480, w1=0.341743, c=0.207411, cost=553.607422
End of epoch 481, w1=0.342185, c=0.207829, cost=553.570374
End of epoch 482, w1=0.342626, c=0.208247, cost=553.533447
End of epoch 483, w1=0.343067, c=0.208665, cost=553.496582
End of epoch 484, w1=0.343507, c=0.209083, cost=553.459778
End of epoch 485, w1=0.343946, c=0.209501, cost=553.423035
End of epoch 486, w1=0.344384, c=0.209919, cost=553.386353
End of epoch 487, w1=0.344821, c=0.210337, cost=553.349854
End of epoch 488, w1=0.345257, c=0.210755, cost=553.313354
End of epoch 489, w1=0.345693, c=0.211173, cost=553.276978
End of epoch 490, w1=0.346128, c=0.211591, cost=553.240601
End of epoch 491, w1=0.346562, c=0.212008, cost=553.204346
End of epoch 492, w1=0.346995, c=0.212426, cost=553.168152
End of epoch 493, w1=0.347428, c=0.212844, cost=553.131958
End of epoch 494, w1=0.347859, c=0.213261, cost=553.095947
End of epoch 495, w1=0.348290, c=0.213679, cost=553.0599

End of epoch 717, w1=0.426553, c=0.305471, cost=546.468750
End of epoch 718, w1=0.426837, c=0.305880, cost=546.443909
End of epoch 719, w1=0.427121, c=0.306290, cost=546.419006
End of epoch 720, w1=0.427404, c=0.306700, cost=546.394226
End of epoch 721, w1=0.427686, c=0.307110, cost=546.369507
End of epoch 722, w1=0.427968, c=0.307519, cost=546.344849
End of epoch 723, w1=0.428249, c=0.307929, cost=546.320129
End of epoch 724, w1=0.428530, c=0.308339, cost=546.295410
End of epoch 725, w1=0.428810, c=0.308748, cost=546.270813
End of epoch 726, w1=0.429090, c=0.309158, cost=546.246277
End of epoch 727, w1=0.429369, c=0.309567, cost=546.221680
End of epoch 728, w1=0.429648, c=0.309977, cost=546.197144
End of epoch 729, w1=0.429926, c=0.310386, cost=546.172729
End of epoch 730, w1=0.430204, c=0.310796, cost=546.148193
End of epoch 731, w1=0.430481, c=0.311205, cost=546.123779
End of epoch 732, w1=0.430757, c=0.311615, cost=546.099365
End of epoch 733, w1=0.431033, c=0.312024, cost=546.0750

End of epoch 952, w1=0.480399, c=0.401042, cost=541.328735
End of epoch 953, w1=0.480580, c=0.401446, cost=541.309143
End of epoch 954, w1=0.480761, c=0.401850, cost=541.289551
End of epoch 955, w1=0.480941, c=0.402253, cost=541.270020
End of epoch 956, w1=0.481121, c=0.402657, cost=541.250488
End of epoch 957, w1=0.481301, c=0.403061, cost=541.230957
End of epoch 958, w1=0.481480, c=0.403465, cost=541.211487
End of epoch 959, w1=0.481659, c=0.403868, cost=541.191956
End of epoch 960, w1=0.481837, c=0.404272, cost=541.172424
End of epoch 961, w1=0.482016, c=0.404676, cost=541.153015
End of epoch 962, w1=0.482194, c=0.405079, cost=541.133545
End of epoch 963, w1=0.482371, c=0.405483, cost=541.114075
End of epoch 964, w1=0.482548, c=0.405887, cost=541.094666
End of epoch 965, w1=0.482725, c=0.406290, cost=541.075256
End of epoch 966, w1=0.482902, c=0.406694, cost=541.055847
End of epoch 967, w1=0.483078, c=0.407097, cost=541.036499
End of epoch 968, w1=0.483254, c=0.407501, cost=541.0170

...

End of epoch 98835, w1=-0.218866, c=19.400629, cost=91.308907
End of epoch 98836, w1=-0.218869, c=19.400705, cost=91.308319
End of epoch 98837, w1=-0.218872, c=19.400782, cost=91.307732
End of epoch 98838, w1=-0.218875, c=19.400858, cost=91.307152
End of epoch 98839, w1=-0.218879, c=19.400934, cost=91.306557
End of epoch 98840, w1=-0.218882, c=19.401011, cost=91.305977
End of epoch 98841, w1=-0.218885, c=19.401087, cost=91.305397
End of epoch 98842, w1=-0.218888, c=19.401163, cost=91.304802
End of epoch 98843, w1=-0.218892, c=19.401239, cost=91.304237
End of epoch 98844, w1=-0.218895, c=19.401316, cost=91.303650
End of epoch 98845, w1=-0.218898, c=19.401392, cost=91.303047
End of epoch 98846, w1=-0.218901, c=19.401468, cost=91.302460
End of epoch 98847, w1=-0.218904, c=19.401545, cost=91.301888
End of epoch 98848, w1=-0.218908, c=19.401621, cost=91.301300
End of epoch 98849, w1=-0.218911, c=19.401697, cost=91.300713
End of epoch 98850, w1=-0.218914, c=19.401773, cost=91.300133
End of e

End of epoch 99086, w1=-0.219681, c=19.419779, cost=91.162613
End of epoch 99087, w1=-0.219684, c=19.419855, cost=91.162033
End of epoch 99088, w1=-0.219687, c=19.419931, cost=91.161438
End of epoch 99089, w1=-0.219691, c=19.420008, cost=91.160866
End of epoch 99090, w1=-0.219694, c=19.420084, cost=91.160294
End of epoch 99091, w1=-0.219697, c=19.420160, cost=91.159714
End of epoch 99092, w1=-0.219700, c=19.420237, cost=91.159126
End of epoch 99093, w1=-0.219704, c=19.420313, cost=91.158539
End of epoch 99094, w1=-0.219707, c=19.420389, cost=91.157959
End of epoch 99095, w1=-0.219710, c=19.420465, cost=91.157387
End of epoch 99096, w1=-0.219713, c=19.420542, cost=91.156807
End of epoch 99097, w1=-0.219717, c=19.420618, cost=91.156227
End of epoch 99098, w1=-0.219720, c=19.420694, cost=91.155632
End of epoch 99099, w1=-0.219723, c=19.420771, cost=91.155067
End of epoch 99100, w1=-0.219726, c=19.420847, cost=91.154480
End of epoch 99101, w1=-0.219730, c=19.420923, cost=91.153893
End of e

End of epoch 99321, w1=-0.220441, c=19.437708, cost=91.026207
End of epoch 99322, w1=-0.220444, c=19.437784, cost=91.025635
End of epoch 99323, w1=-0.220447, c=19.437860, cost=91.025055
End of epoch 99324, w1=-0.220451, c=19.437937, cost=91.024475
End of epoch 99325, w1=-0.220454, c=19.438013, cost=91.023903
End of epoch 99326, w1=-0.220457, c=19.438089, cost=91.023323
End of epoch 99327, w1=-0.220460, c=19.438166, cost=91.022743
End of epoch 99328, w1=-0.220464, c=19.438242, cost=91.022171
End of epoch 99329, w1=-0.220467, c=19.438318, cost=91.021591
End of epoch 99330, w1=-0.220470, c=19.438395, cost=91.021004
End of epoch 99331, w1=-0.220473, c=19.438471, cost=91.020439
End of epoch 99332, w1=-0.220477, c=19.438547, cost=91.019852
End of epoch 99333, w1=-0.220480, c=19.438623, cost=91.019272
End of epoch 99334, w1=-0.220483, c=19.438700, cost=91.018677
End of epoch 99335, w1=-0.220486, c=19.438776, cost=91.018112
End of epoch 99336, w1=-0.220489, c=19.438852, cost=91.017525
End of e

End of epoch 99567, w1=-0.221236, c=19.456476, cost=90.884018
End of epoch 99568, w1=-0.221240, c=19.456553, cost=90.883430
End of epoch 99569, w1=-0.221243, c=19.456629, cost=90.882874
End of epoch 99570, w1=-0.221246, c=19.456705, cost=90.882286
End of epoch 99571, w1=-0.221249, c=19.456781, cost=90.881721
End of epoch 99572, w1=-0.221253, c=19.456858, cost=90.881142
End of epoch 99573, w1=-0.221256, c=19.456934, cost=90.880562
End of epoch 99574, w1=-0.221259, c=19.457010, cost=90.879974
End of epoch 99575, w1=-0.221262, c=19.457087, cost=90.879402
End of epoch 99576, w1=-0.221266, c=19.457163, cost=90.878822
End of epoch 99577, w1=-0.221269, c=19.457239, cost=90.878250
End of epoch 99578, w1=-0.221272, c=19.457315, cost=90.877670
End of epoch 99579, w1=-0.221275, c=19.457392, cost=90.877090
End of epoch 99580, w1=-0.221278, c=19.457468, cost=90.876526
End of epoch 99581, w1=-0.221282, c=19.457544, cost=90.875938
End of epoch 99582, w1=-0.221285, c=19.457621, cost=90.875359
End of e

End of epoch 99799, w1=-0.221985, c=19.473930, cost=90.752312
End of epoch 99800, w1=-0.221988, c=19.474005, cost=90.751755
End of epoch 99801, w1=-0.221992, c=19.474079, cost=90.751175
End of epoch 99802, w1=-0.221995, c=19.474154, cost=90.750641
End of epoch 99803, w1=-0.221998, c=19.474228, cost=90.750061
End of epoch 99804, w1=-0.222001, c=19.474302, cost=90.749504
End of epoch 99805, w1=-0.222004, c=19.474377, cost=90.748947
End of epoch 99806, w1=-0.222008, c=19.474451, cost=90.748390
End of epoch 99807, w1=-0.222011, c=19.474525, cost=90.747826
End of epoch 99808, w1=-0.222014, c=19.474600, cost=90.747269
End of epoch 99809, w1=-0.222017, c=19.474674, cost=90.746704
End of epoch 99810, w1=-0.222021, c=19.474749, cost=90.746132
End of epoch 99811, w1=-0.222024, c=19.474823, cost=90.745575
End of epoch 99812, w1=-0.222027, c=19.474897, cost=90.745026
End of epoch 99813, w1=-0.222030, c=19.474972, cost=90.744469
End of epoch 99814, w1=-0.222033, c=19.475046, cost=90.743896
End of e

In [5]:
# use best_w1 and best_c to make predictions on all observations in the test set
predictions = df_boston_test_features['CRIM'].values * best_w1 + best_c

# compute MSE on test set
from sklearn.metrics import mean_squared_error
mse_test = mean_squared_error(np.transpose(df_boston_test_target.values), predictions)
print (mse_test)

85.05865369536087
